In [30]:
! pip install pypdf

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [1]:
import os
import logging
from pathlib import Path
import requests
import pandas as pd
from transformers import AutoTokenizer
from sentence_transformers import SentenceTransformer

from docling.datamodel.base_models import ConversionStatus, InputFormat
from docling.datamodel.document import ConversionResult
from docling.datamodel.pipeline_options import PdfPipelineOptions
from docling.document_converter import DocumentConverter, PdfFormatOption
from docling.chunking import HybridChunker

In [2]:
# Logger setup
logging.basicConfig(level=logging.INFO)
_log = logging.getLogger(__name__)

# Base URL for PDFs
BASE_URL = 'https://raw.githubusercontent.com/DS4SD/docling/refs/heads/main/tests/data/pdf/'
PDF_FILES = [
    '2203.01017v2.pdf', '2305.03393v1-pg9.pdf', '2305.03393v1.pdf',
    'amt_handbook_sample.pdf', 'code_and_formula.pdf', 'picture_classification.pdf',
    'redp5110_sampled.pdf', 'right_to_left_01.pdf', 'right_to_left_02.pdf', 'right_to_left_03.pdf'
]
INPUT_DOC_PATHS = [os.path.join(BASE_URL, pdf_file) for pdf_file in PDF_FILES]

# Configure PDF processing
pipeline_options = PdfPipelineOptions()
pipeline_options.generate_page_images = True

doc_converter = DocumentConverter(
    format_options={InputFormat.PDF: PdfFormatOption(pipeline_options=pipeline_options)}
)

# Load tokenizer and embedding model
EMBED_MODEL_ID = "sentence-transformers/all-MiniLM-L6-v2"
MAX_TOKENS = 64  # Small token limit for demonstration

In [3]:
tokenizer = AutoTokenizer.from_pretrained(EMBED_MODEL_ID)
embedding_model = SentenceTransformer(EMBED_MODEL_ID)

chunker = HybridChunker(tokenizer=tokenizer, max_tokens=MAX_TOKENS, merge_peers=True)

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-MiniLM-L6-v2


In [19]:
def embed_text(text: str) -> list[float]:
    """Generate an embedding for a given text."""
    return embedding_model.encode([text], normalize_embeddings=True).tolist()[0]

def generate_document_rows(conv_results):
    """
    Generator that yields one row per chunk from each successfully converted document.
    Each yielded dict contains:
      - file_name: Name of the source file.
      - raw_markdown: Serialized text for the chunk.
      - chunk_embedding: The embedding vector for that chunk.
    """
    processed_docs = 0
    for conv_res in conv_results:
        if conv_res.status != ConversionStatus.SUCCESS:
            continue

        processed_docs += 1
        file_name = conv_res.input.file.stem  # FIX: Use `.file.stem` instead of `.path`

        # Extract the document object (which contains iterate_items)
        document = conv_res.document
        try:
            document_markdown = document.export_to_markdown()
        except:
            document_markdown = ""
        if document is None:
            _log.warning(f"Document conversion failed for {file_name}")
            continue

        # Process each chunk from the document
        for chunk in chunker.chunk(dl_doc=document):  # Use `document` here!
            raw_chunk = chunker.serialize(chunk=chunk)
            embedding = embed_text(raw_chunk)
            yield {
                "file_name": file_name,
                "full_document_markdown": document_markdown,
                "raw_chunk_markdown": raw_chunk,
                "chunk_embedding": embedding,
            }
    _log.info(f"Processed {processed_docs} documents successfully.")

In [ ]:
doc_converter.convert_all(

In [20]:
# Convert documents
conv_results = doc_converter.convert_all(INPUT_DOC_PATHS, raises_on_error=False)

# Build a DataFrame where each row is a unique chunk record
rows = list(generate_document_rows(conv_results))

INFO:docling.document_converter:Going to convert document batch...
INFO:docling.pipeline.base_pipeline:Processing document 2203.01017v2.pdf
INFO:docling.document_converter:Finished converting document 2203.01017v2.pdf in 56.78 sec.
/Users/farceo/dev/feast/.venv/lib/python3.11/site-packages/docling_core/transforms/chunker/hybrid_chunker.py:176: UserWarning: Headers and captions for this chunk are longer than the total amount of size for the chunk, chunk will be ignored: doc_chunk.text='PubTabNet, Tags = 3. PubTabNet, Bbox = 3. PubTabNet, Size = 509k. PubTabNet, Format = PNG. FinTabNet, Tags = 3. FinTabNet, Bbox = 3. FinTabNet, Size = 112k. FinTabNet, Format = PDF. TableBank, Tags = 3. TableBank, Bbox = 7. TableBank, Size = 145k. TableBank, Format = JPEG. Combined-Tabnet(*), Tags = 3. Combined-Tabnet(*), Bbox = 3. Combined-Tabnet(*), Size = 400k. Combined-Tabnet(*), Format = PNG. Combined(**), Tags = 3. Combined(**), Bbox = 3. Combined(**), Size = 500k. Combined(**), Format = PNG. SynthT

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO:__main__:Processed 10 documents successfully.


In [21]:
df = pd.DataFrame.from_records(rows)

In [28]:
df.head()

file_name                             full_document_markdown  \
0  2203.01017v2  ## TableFormer: Table Structure Understanding ...   
1  2203.01017v2  ## TableFormer: Table Structure Understanding ...   
2  2203.01017v2  ## TableFormer: Table Structure Understanding ...   
3  2203.01017v2  ## TableFormer: Table Structure Understanding ...   
4  2203.01017v2  ## TableFormer: Table Structure Understanding ...   

                                  raw_chunk_markdown  \
0  Ahmed Nassar, Nikolaos Livathinos, Maksym Lysa...   
1  a. Picture of a table:\nTables organize valuab...   
2  a. Picture of a table:\ncomplex column/row-hea...   
3  a. Picture of a table:\nmodel. The latter impr...   
4  a. Picture of a table:\nwe can obtain the cont...   

                                     chunk_embedding  
0  [-0.056879762560129166, 0.01667858101427555, -...  
1  [0.050771258771419525, -0.0055733839981257915,...  
2  [-0.05088765174150467, 0.05101901665329933, -0...  
3  [0.011835305020213127, -0.09409898519515991, 0...  
4  [-0.0068757119588553905, 0.006624480709433556,...

In [29]:
df.to_parquet('docling_samples.parquet', index=False)

In [ ]:
BASE_URL = 'https://raw.githubusercontent.com/DS4SD/docling/refs/heads/main/tests/data/pdf/'
PDF_FILES = [
    '2203.01017v2.pdf', '2305.03393v1-pg9.pdf', '2305.03393v1.pdf',
    'amt_handbook_sample.pdf', 'code_and_formula.pdf', 'picture_classification.pdf',
    'redp5110_sampled.pdf', 'right_to_left_01.pdf', 'right_to_left_02.pdf', 'right_to_left_03.pdf'
]

In [48]:
output_dict = {}
for file_name in PDF_FILES:
    try:
        r = requests.get(BASE_URL + file_name)
        pdf_bytes = io.BytesIO(r.content)
        output_dict[file_name] = pdf_bytes.getvalue()
    except Exception as e:
        print(f"error with {file_name} \n{e}")

In [31]:
r = requests.get(BASE_URL + PDF_FILES[0])

In [33]:
import pypdf

In [36]:
import io

In [38]:
pdf_example = pypdf.PdfReader(io.BytesIO(r.content))

In [39]:
pdf_example